### Sarath chandra Makkena (Keras Regression and Light GBM)

In [2]:
import numpy as np 
import pandas as pd 
import sklearn
import seaborn as sns
import matplotlib.pyplot as plt
import os
import shutil
from sklearn.model_selection import train_test_split
from math import radians, cos, sin, asin, sqrt
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
import pandas_profiling
#from google.colab import drive ## <--  comment this line if u want to run this code on local
#drive.mount('/content/drive')  ## <-- even this , as these are to mount google drive to collab


### loading data into dataframe

In [3]:
df1 =  pd.read_csv('Match_Info - Match_Info.csv')
df2 = pd.read_csv('Delivery_Info - Delivery_Info.csv')

In [91]:
print(df1.shape)
print(df2.shape)

(756, 17)
(179058, 21)


In [92]:
df2

Match_ID  Innings                 Batting_Team  \
0              1        1                Pune Warriors   
1              1        1                Pune Warriors   
2              1        1                Pune Warriors   
3              1        1                Pune Warriors   
4              1        1                Pune Warriors   
...          ...      ...                          ...   
179053       756        2  Royal Challengers Bangalore   
179054       756        2  Royal Challengers Bangalore   
179055       756        2  Royal Challengers Bangalore   
179056       756        2  Royal Challengers Bangalore   
179057       756        2  Royal Challengers Bangalore   

                       Bowling_Team  Over  Ball     Batsman     Non_Striker  \
0                  Delhi Daredevils     1     1  RV Uthappa        AJ Finch   
1                  Delhi Daredevils     1     2  RV Uthappa        AJ Finch   
2                  Delhi Daredevils     1     3  RV Uthappa        AJ Finch   
3                  Delhi Daredevils     1     4  RV Uthappa        AJ Finch   
4                  Delhi Daredevils     1     5  RV Uthappa        AJ Finch   
...                             ...   ...   ...         ...             ...   
179053  Royal Challengers Bangalore    20     1     V Kohli  Mohammed Siraj   
179054  Royal Challengers Bangalore    20     3     V Kohli  Mohammed Siraj   
179055  Royal Challengers Bangalore    20     3     V Kohli  Mohammed Siraj   
179056  Royal Challengers Bangalore    20     5     V Kohli  Mohammed Siraj   
179057  Royal Challengers Bangalore    20     6     V Kohli  Mohammed Siraj   

           Bowler  Is_Super_Over  ...  Bye_Runs  Legbye_Runs  Noball_Runs  \
0       IK Pathan              0  ...         0            0            0   
1       IK Pathan              0  ...         0            0            0   
2       IK Pathan              0  ...         0            0            0   
3       IK Pathan              0  ...         0            0            0   
4       IK Pathan              0  ...         0            0            0   
...           ...            ...  ...       ...          ...          ...   
179053  JJ Bumrah              0  ...         0            0            0   
179054  JJ Bumrah              0  ...         0            0            0   
179055  JJ Bumrah              0  ...         0            0            0   
179056  JJ Bumrah              0  ...         0            0            0   
179057  JJ Bumrah              0  ...         0            0            0   

        Penalty_Runs  Batsman_Runs  Extras  Total_Runs  Player_Dismissed  \
0                  0             0       0           0               NaN   
1                  0             2       0           2               NaN   
2                  0             4       0           4               NaN   
3                  0             0       0           0               NaN   
4                  0             1       0           1               NaN   
...              ...           ...     ...         ...               ...   
179053             0             4       0           4               NaN   
179054             0             0       0           0               NaN   
179055             0             6       0           6               NaN   
179056             0             0       0           0               NaN   
179057             0             0       0           0               NaN   

       Dismissal_Type Fielder  
0                 NaN     NaN  
1                 NaN     NaN  
2                 NaN     NaN  
3                 NaN     NaN  
4                 NaN     NaN  
...               ...     ...  
179053            NaN     NaN  
179054            NaN     NaN  
179055            NaN     NaN  
179056            NaN     NaN  
179057            NaN     NaN  

[179058 rows x 21 columns]

In [93]:
df2['Match_Innings'] = df2['Match_ID'].astype(str) + df2['Innings'].astype(str)

In [94]:
df2['Match_Innings'].describe()

count     179058
unique      1528
top         4532
freq         134
Name: Match_Innings, dtype: object

In [95]:
values_iin, counts_inn = np.unique(df2['Match_Innings'], return_counts=True)
print(counts_inn)

[122 124 126 ... 112 124 120]


In [96]:
df2.loc[df2.index==122,'Match_Innings'].values[0]

'11'

In [97]:
i1= 11
arr_inn =[]
tot_balls_per_inning = 0
for l1 in range(len(df2.index)):
    if(df2.loc[df2.index==l1,'Match_Innings'].values[0] == i1):
        tot_balls_per_inning = tot_balls_per_inning+1
        #print(tot_balls_per_inning)
    else:
        #print(tot_balls_per_inning)
        arr_inn.append(tot_balls_per_inning)
        tot_balls_per_inning = 0       
        i1 = df2.loc[df2.index==l1,'Match_Innings'].values[0]
        
arr_inn.append(tot_balls_per_inning)

In [98]:
del arr_inn[0]

In [99]:
len(arr_inn)

1528

In [100]:
neww_inn =[]
for l in range(len(arr_inn)):
    for c in range(counts_inn[l]):
        neww_inn.append(arr_inn[l])
    l = l+1  

In [101]:
len(neww_inn)

179058

In [102]:
df2['balls_inning'] = np.array(neww_inn)

In [103]:
df2.describe()

Match_ID        Innings           Over           Ball  \
count  179058.000000  179058.000000  179058.000000  179058.000000   
mean      378.453451       1.482966      10.162701       3.193379   
std       217.984428       0.501875       5.677712       1.946118   
min         1.000000       1.000000       1.000000       0.000000   
25%       190.000000       1.000000       5.000000       1.000000   
50%       379.000000       1.000000      10.000000       3.000000   
75%       567.000000       2.000000      15.000000       5.000000   
max       756.000000       4.000000      20.000000       9.000000   

       Is_Super_Over      Wide_Runs  Bye_Runs  Legbye_Runs  Noball_Runs  \
count  179058.000000  179058.000000  179058.0     179058.0     179058.0   
mean        0.013057       0.036759       0.0          0.0          0.0   
std         0.113520       0.251237       0.0          0.0          0.0   
min         0.000000       0.000000       0.0          0.0          0.0   
25%         0.000000       0.000000       0.0          0.0          0.0   
50%         0.000000       0.000000       0.0          0.0          0.0   
75%         0.000000       0.000000       0.0          0.0          0.0   
max         1.000000       5.000000       0.0          0.0          0.0   

       Penalty_Runs   Batsman_Runs         Extras     Total_Runs  \
count      179058.0  179058.000000  179058.000000  179058.000000   
mean            0.0       1.237772       0.067107       1.304879   
std             0.0       1.610132       0.342754       1.598228   
min             0.0       0.000000       0.000000       0.000000   
25%             0.0       0.000000       0.000000       0.000000   
50%             0.0       1.000000       0.000000       1.000000   
75%             0.0       1.000000       0.000000       1.000000   
max             0.0       6.000000       7.000000       7.000000   

        balls_inning  
count  179058.000000  
mean      116.181014  
std        18.403574  
min         2.000000  
25%       118.000000  
50%       122.000000  
75%       124.000000  
max       133.000000

In [53]:
df2.to_csv('balls_innings.csv')

In [55]:
df2

Match_ID  Innings                 Batting_Team  \
0              1        1                Pune Warriors   
1              1        1                Pune Warriors   
2              1        1                Pune Warriors   
3              1        1                Pune Warriors   
4              1        1                Pune Warriors   
...          ...      ...                          ...   
179053       756        2  Royal Challengers Bangalore   
179054       756        2  Royal Challengers Bangalore   
179055       756        2  Royal Challengers Bangalore   
179056       756        2  Royal Challengers Bangalore   
179057       756        2  Royal Challengers Bangalore   

                       Bowling_Team  Over  Ball     Batsman     Non_Striker  \
0                  Delhi Daredevils     1     1  RV Uthappa        AJ Finch   
1                  Delhi Daredevils     1     2  RV Uthappa        AJ Finch   
2                  Delhi Daredevils     1     3  RV Uthappa        AJ Finch   
3                  Delhi Daredevils     1     4  RV Uthappa        AJ Finch   
4                  Delhi Daredevils     1     5  RV Uthappa        AJ Finch   
...                             ...   ...   ...         ...             ...   
179053  Royal Challengers Bangalore    20     1     V Kohli  Mohammed Siraj   
179054  Royal Challengers Bangalore    20     3     V Kohli  Mohammed Siraj   
179055  Royal Challengers Bangalore    20     3     V Kohli  Mohammed Siraj   
179056  Royal Challengers Bangalore    20     5     V Kohli  Mohammed Siraj   
179057  Royal Challengers Bangalore    20     6     V Kohli  Mohammed Siraj   

           Bowler  Is_Super_Over  ...  Noball_Runs  Penalty_Runs  \
0       IK Pathan              0  ...            0             0   
1       IK Pathan              0  ...            0             0   
2       IK Pathan              0  ...            0             0   
3       IK Pathan              0  ...            0             0   
4       IK Pathan              0  ...            0             0   
...           ...            ...  ...          ...           ...   
179053  JJ Bumrah              0  ...            0             0   
179054  JJ Bumrah              0  ...            0             0   
179055  JJ Bumrah              0  ...            0             0   
179056  JJ Bumrah              0  ...            0             0   
179057  JJ Bumrah              0  ...            0             0   

        Batsman_Runs  Extras  Total_Runs  Player_Dismissed  Dismissal_Type  \
0                  0       0           0               NaN             NaN   
1                  2       0           2               NaN             NaN   
2                  4       0           4               NaN             NaN   
3                  0       0           0               NaN             NaN   
4                  1       0           1               NaN             NaN   
...              ...     ...         ...               ...             ...   
179053             4       0           4               NaN             NaN   
179054             0       0           0               NaN             NaN   
179055             6       0           6               NaN             NaN   
179056             0       0           0               NaN             NaN   
179057             0       0           0               NaN             NaN   

        Fielder Match_Innings balls_inning  
0           NaN            11          122  
1           NaN            11          122  
2           NaN            11          122  
3           NaN            11          122  
4           NaN            11          122  
...         ...           ...          ...  
179053      NaN          7562          123  
179054      NaN          7562          123  
179055      NaN          7562          123  
179056      NaN          7562          123  
179057      NaN          7562          123  

[179058 rows x 23 columns]

In [17]:
df2 = pd.read_csv('innings_csv.csv')

In [4]:
merged_inner = pd.merge(left=df1,right=df2, left_on='Match_ID', right_on='Match_ID')

In [6]:
merged_inner.profile_report(style={'full_width':True})

/Users/sarathchandra/venv/lib/python3.7/site-packages/pandas_profiling/model/correlations.py:34: RuntimeWarning: invalid value encountered in double_scalars
  return np.sqrt(phi2corr / min((kcorr - 1.0), (rcorr - 1.0)))


In [105]:
Batting_Team =  pd.get_dummies(merged_inner['Batting_Team'],dummy_na=False)
merged_inner = merged_inner.drop(merged_inner[['Batting_Team']],axis=1)
merged_inner = pd.concat([merged_inner,Batting_Team],axis=1)

In [106]:
Batsman =  pd.get_dummies(merged_inner['Bowler'],dummy_na=False)
merged_inner = merged_inner.drop(merged_inner[['Bowler']],axis=1)
merged_inner = pd.concat([merged_inner,Batsman],axis=1)

In [107]:
Extras =  pd.get_dummies(merged_inner['Extras'],dummy_na=False)
merged_inner = merged_inner.drop(merged_inner[['Extras']],axis=1)
merged_inner = pd.concat([merged_inner,Extras],axis=1)
Wide_Runs =  pd.get_dummies(merged_inner['Wide_Runs'],dummy_na=False)
merged_inner = merged_inner.drop(merged_inner[['Wide_Runs']],axis=1)
merged_inner = pd.concat([merged_inner,Wide_Runs],axis=1)
Venue =  pd.get_dummies(merged_inner['Venue'],dummy_na=False)
merged_inner = merged_inner.drop(merged_inner[['Venue']],axis=1)
merged_inner = pd.concat([merged_inner,Venue],axis=1)

In [108]:
merged_inner.drop(['Umpire3','Fielder','Dismissal_Type','Player_Dismissed','Win_By_Runs','Match_Innings','Win_By_Wicket','Winner'],axis=1, inplace = True)

In [109]:
merged_inner.shape

(179058, 494)

In [111]:
merged_inner = merged_inner.dropna()

In [112]:
merged_inner.isnull().sum().sort_values(ascending = False)

Wankhede Stadium    0
F du Plessis        0
FY Fazal            0
GB Hogg             0
GC Viljoen          0
                   ..
RR Bhatkal          0
RR Bose             0
RR Powar            0
RR Raje             0
Match_ID            0
Length: 494, dtype: int64

In [113]:
listtt = list(merged_inner.select_dtypes(include=['object']).columns)

In [114]:
for l in listtt:
    print(l)

Date
Team1
Team2
Toss_Winner
Toss_Decision
result
Man_Of_The_Match
Umpire1
Umpire2
Bowling_Team
Batsman
Non_Striker


In [115]:
merged_inner.drop(listtt , axis = 1,inplace = True)

In [116]:
merged_inner.shape

(178686, 482)

In [117]:
df2['balls_inning'].describe()

count    179058.000000
mean        116.181014
std          18.403574
min           2.000000
25%         118.000000
50%         122.000000
75%         124.000000
max         133.000000
Name: balls_inning, dtype: float64

Check for null values in both train and test set

In [118]:
merged_inner.dtypes

Match_ID                                        int64
Season                                          int64
DL_Method                                       int64
Innings                                         int64
Over                                            int64
                                                ...  
St George's Park                                uint8
Subrata Roy Sahara Stadium                      uint8
SuperSport Park                                 uint8
Vidarbha Cricket Association Stadium, Jamtha    uint8
Wankhede Stadium                                uint8
Length: 482, dtype: object

In [8]:
merged_inner['Winner'].unique().tolist()

['Pune Warriors',
 'Delhi Daredevils',
 'Royal Challengers Bangalore',
 'Gujarat Lions',
 'Mumbai Indians',
 'Rising Pune Supergiants',
 'Kolkata Knight Riders',
 'Chennai Super Kings',
 'Rajasthan Royals',
 'Kings XI Punjab',
 'Kochi Tuskers Kerala',
 'Deccan Chargers',
 'Sunrisers Hyderabad',
 nan,
 'Delhi Capitals',
 'Rising Pune Supergiant']

In [175]:
merged_inner.dtypes

Match_ID                                         int64
Season                                           int64
Date                                            object
Team1                                           object
Team2                                           object
                                                 ...  
St George's Park                                 uint8
Subrata Roy Sahara Stadium                       uint8
SuperSport Park                                  uint8
Vidarbha Cricket Association Stadium, Jamtha     uint8
Wankhede Stadium                                 uint8
Length: 610, dtype: object

In [190]:
mylist

['Date',
 'Team1',
 'Team2',
 'Toss_Winner',
 'Toss_Decision',
 'result',
 'Winner',
 'Man_Of_The_Match',
 'Umpire1',
 'Umpire2',
 'Bowling_Team',
 'Non_Striker',
 'Bowler',
 'Player_Dismissed',
 'Dismissal_Type',
 'Fielder']

In [189]:
mylist = list(merged_inner.select_dtypes(include=['object']).columns)

In [104]:
for col in merged_inner.columns:
    print(col)
    print(merged_inner[col].unique().tolist())
    print("\n")

Match_ID
[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220

In [40]:
merged_inner.dtypes

Match_ID                                         int64
Season                                           int64
Date                                            object
Team1                                           object
Team2                                           object
                                                 ...  
St George's Park                                 uint8
Subrata Roy Sahara Stadium                       uint8
SuperSport Park                                  uint8
Vidarbha Cricket Association Stadium, Jamtha     uint8
Wankhede Stadium                                 uint8
Length: 605, dtype: object

In [80]:
values, counts = np.unique(df2['Match_ID'], return_counts=True)

[  1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17  18
  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35  36
  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53  54
  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71  72
  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89  90
  91  92  93  94  95  96  97  98  99 100 101 102 103 104 105 106 107 108
 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126
 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144
 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162
 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180
 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198
 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216
 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234
 235 236 237 238 239 240 241 242 243 244 245 246 24

In [77]:
i= 1
p=0
arr =[]
tot_runs_per_match = 0
for l in range(len(df2.index)):
    if(df2.loc[df2.index==l,'Match_ID'].values[0] == i and df2[innin]):
        tot_runs_per_match = tot_runs_per_match + df2.loc[df2.index==l,'Total_Runs'].values[0]
    if(df2.loc[df2.index==l,'Match_ID'].values[0] == i+1):
        print(i)
        arr.append(tot_runs_per_match)
        tot_runs_per_match = 0       
        i = i+1

arr.append(tot_runs_per_match)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
27

In [91]:
len(arr)
neww =[]
for l in range(len(arr)):
    for c in range(counts[l]):
        neww.append(arr[l])
    l = l+1  

In [160]:
merged_inner.runs_inning

0         172
1         172
2         172
3         172
4         172
         ... 
179053    167
179054    167
179055    167
179056    167
179057    167
Name: runs_inning, Length: 179058, dtype: int64

In [168]:
numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64','uint8']
merged_inner.select_dtypes(include=numerics)

Match_ID  Season  DL_Method  Win_By_Runs  Win_By_Wicket  Umpire3  \
0              1    2013          0         38.0            NaN      NaN   
1              1    2013          0         38.0            NaN      NaN   
2              1    2013          0         38.0            NaN      NaN   
3              1    2013          0         38.0            NaN      NaN   
4              1    2013          0         38.0            NaN      NaN   
...          ...     ...        ...          ...            ...      ...   
179053       756    2018          0         46.0            NaN      NaN   
179054       756    2018          0         46.0            NaN      NaN   
179055       756    2018          0         46.0            NaN      NaN   
179056       756    2018          0         46.0            NaN      NaN   
179057       756    2018          0         46.0            NaN      NaN   

        Innings  Over  Ball  Is_Super_Over  ...  \
0             1     1     1              0  ...   
1             1     1     2              0  ...   
2             1     1     3              0  ...   
3             1     1     4              0  ...   
4             1     1     5              0  ...   
...         ...   ...   ...            ...  ...   
179053        2    20     1              0  ...   
179054        2    20     3              0  ...   
179055        2    20     3              0  ...   
179056        2    20     5              0  ...   
179057        2    20     6              0  ...   

        Saurashtra Cricket Association Stadium  Sawai Mansingh Stadium  \
0                                            0                       0   
1                                            0                       0   
2                                            0                       0   
3                                            0                       0   
4                                            0                       0   
...                                        ...                     ...   
179053                                       0                       0   
179054                                       0                       0   
179055                                       0                       0   
179056                                       0                       0   
179057                                       0                       0   

        Shaheed Veer Narayan Singh International Stadium  \
0                                                      0   
1                                                      0   
2                                                      0   
3                                                      0   
4                                                      0   
...                                                  ...   
179053                                                 0   
179054                                                 0   
179055                                                 0   
179056                                                 0   
179057                                                 0   

        Sharjah Cricket Stadium  Sheikh Zayed Stadium  St George's Park  \
0                             0                     0                 0   
1                             0                     0                 0   
2                             0                     0                 0   
3                             0                     0                 0   
4                             0                     0                 0   
...                         ...                   ...               ...   
179053                        0                     0                 0   
179054                        0                     0                 0   
179055                        0                     0                 0   
179056                        0                     0                 0   
179057                        0                

In [262]:
merged_inner.dtypes

Match_ID                                          int64
Season                                            int64
DL_Method                                         int64
Win_By_Runs                                     float64
Win_By_Wicket                                   float64
                                                 ...   
St George's Park                                  uint8
Subrata Roy Sahara Stadium                        uint8
SuperSport Park                                   uint8
Vidarbha Cricket Association Stadium, Jamtha      uint8
Wankhede Stadium                                  uint8
Length: 594, dtype: object

In [119]:
y = merged_inner.balls_inning
merged_inner = merged_inner.drop('balls_inning', axis = 1)

In [120]:
train_x, test_x, train_y, test_y = train_test_split(merged_inner, y, test_size = 0.2, random_state = 44) 

In [121]:
from sklearn.metrics import mean_squared_error

In [122]:
import shutil
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression

lm = LinearRegression()
lm.fit(train_x, train_y)
y_pred = lm.predict(test_x)

from sklearn.metrics import mean_squared_error

print('Test RMSE %.3f'%(np.sqrt(mean_squared_error(y_pred, test_y))))

Test RMSE 176928.106


In [124]:
## Random Forest Regression 
from sklearn.ensemble import RandomForestRegressor

rf = RandomForestRegressor(max_depth = 40, random_state = 42, n_estimators = 1000)
rf.fit(train_x, train_y)
rf_pred = rf.predict(test_x)
print('Test RMSE %.3f'%(np.sqrt(mean_squared_error(rf_pred, test_y))))

Test RMSE 2.941
